### Prepare methods

In [1]:
import skeletor as sk
import trimesh as tm
import matplotlib.pyplot as plt
import numpy as np
import os
from scipy.spatial import Delaunay
from skeletor import Skeleton
import pandas as pd

In [2]:
def show1(lines, points):
    path = tm.path.Path3D(entities=lines, vertices=points)
    scene = tm.Scene()
    scene.add_geometry(path)
    scene.show
def export_to_excel(data):
    flattened_data = []
    for key, value_list in data.items():
        for value in value_list:
            # 为每个子字典添加一个 'Key' 列
            value['Key'] = key
            flattened_data.append(value)
            # 将展开后的数据转换为 DataFrame
    df = pd.DataFrame(flattened_data)

    # 导出为 Excel 文件
    df.to_excel('output.xlsx', index=False)
class Node:
  def __init__(self, id=None, coords=[]):
    self.id = id
    self.coords= coords
class Branch:
  def __init__(self, branch_num=None, end_node=None, start_node=None, interval_node=[], edge_raddi=None, edge_angle=0):
    self.branch_num = branch_num
    self.end_node = end_node
    self.start_node = start_node
    self.edge_raddi = edge_raddi
    self.edge_angle = edge_angle
    self.interval_node = interval_node
def get_branch(branch_num, start_node_id, end_node_id, interval_nodes):
  start_node = Node(id=start_node_id, coords=skel.vertices[start_node_id])
  end_node = Node(id=end_node_id, coords=skel.vertices[end_node_id])
  branch = Branch(branch_num=branch_num,start_node=start_node, end_node=end_node, interval_node=interval_nodes)
  return branch
def get_tree(edge_map, current_node_id, start_node_id, res, 
               branch_num, Branch, Node, interval = False, interval_nodes=[]):
  # print("-----------------")
  # print("Branch Num:", branch_num)
  # print("current node:", current_node_id)
  # print("start_node:", start_node_id)
  # print([node.id for node in interval_nodes])
  if current_node_id in edge_map:
    if interval and len(edge_map[current_node_id]) == 1:
      # in the interval
      node = Node(id=current_node_id, coords=skel.vertices[current_node_id])
      interval_nodes.append(node)
    if len(edge_map[current_node_id]) == 1:
      # go to next node
      current_node_id = edge_map[current_node_id][0]
      res = get_tree(edge_map, current_node_id, start_node_id, res,
                            branch_num, Branch, Node, interval=True, interval_nodes=interval_nodes)
    else:
      # add the whole branch
      branch_num += 1
      end_node_id = current_node_id
      #radii = radius[start_node_id]
      br = get_branch(branch_num, start_node_id, end_node_id, interval_nodes)
      if branch_num not in res: res[branch_num] = [br]
      else: res[branch_num].append(br)
      start_node_id = current_node_id  
      for node in edge_map[current_node_id]:
        current_node_id = node
        res = get_tree(edge_map, current_node_id, start_node_id, res,
                            branch_num, Branch, Node, interval=False, interval_nodes=[])
    return res
  else:
    branch_num += 1
    end_node_id = current_node_id
    br = get_branch(branch_num, start_node_id, end_node_id, interval_nodes)
    if branch_num not in res: res[branch_num] = [br]
    else: res[branch_num].append(br)
    return res
def reverse_tree(tree, new_root):
    # 构建原始树的逆向映射
    parent_map = {}
    for parent, children in tree.items():
        for child in children:
            if child in parent_map:
                parent_map[child].append(parent)
            else:
                parent_map[child] = [parent]

    # 使用新根节点构建新的树
    new_tree = {new_root: []} 
    print("tree:", tree)
    print("parent_map:",parent_map)
    print("new_tree:",new_tree)

    def add_child(tree, child_nodes, new_tree):
        for child_node in child_nodes:
            if child_node in tree:
                new_tree[child_node] = tree[child_node]
                child_nodes = tree[child_node]
                new_tree = add_child(tree, child_nodes, new_tree)     
        return new_tree
            
    def build_tree(node, new_tree, tree, pre_node=None):
        # tree : {1: [2], 2: [3, 4], 3: [5]}
        # parent_map : {2: [1], 3: [2], 4: [2], 5: [3]}
        # new_tree : {5: [3], 3: [2], 2: [1, 4]}
        # node : 5
        if node in parent_map:
          #print(new_tree, parent_map[node])
          for parent_node in parent_map[node]:
              # parent_node -> child_node BECOME child_node -> parent_node
              if node in new_tree:
                  new_tree[node].append(parent_node)
              else:
                  new_tree[node] = [parent_node]
              
              # add original child node to new tree and child node's children are also added
              if node in tree:
                  for child_node in tree[node]:
                      if child_node != pre_node:
                        new_tree[node].append(child_node)
                        new_tree = add_child(tree, [child_node], new_tree)

              # recursive
              if parent_node in tree:
                  pre_node = node
                  new_tree = build_tree(parent_node, new_tree, tree, pre_node)
        return new_tree
    
    new_tree = build_tree(new_root, new_tree,tree)
    return new_tree
def get_relation(res):
  branch_num = 1
  res_map = {}
  while branch_num in res:
    brs = res[branch_num]
    for br in brs:
      res_map[br.start_node.id] = br.branch_num
      for node in br.interval_node:
        res_map[node.id] = br.branch_num
      res_map[br.end_node.id] = br.branch_num if br.end_node else None
    print(res_map)
    branch_num += 1
  return res_map
class TreeNode:
    def __init__(self, value, coords, parent=None):
        self.value = value
        self.level = None
        self.coords = coords
        self.children = []
        self.parent = parent
        self.edges = {}

    def add_child(self, child_node, edge_radii=None, edge_length=None, edge_angle=None):
        self.children.append(child_node)
        self.edges[child_node] = {'radii': edge_radii, 'length':edge_length, 'angle':edge_angle}

from collections import deque, defaultdict       
def assign_levels(root, branch_num={}):
    # 使用队列进行广度优先搜索，记录每个节点的深度
    queue = deque([(root, 0)])
    node_depth = defaultdict(int)
    node_depth[0] = [root]
    leaf_nodes = []

    while queue:
        node, depth = queue.popleft()
        is_leaf = True
        for child in node.children:
            queue.append((child, depth + 1))
            if depth + 1 not in node_depth:
                node_depth[depth + 1] = [child]
            else:
                node_depth[depth + 1].append(child)
            is_leaf = False
        if is_leaf:
            leaf_nodes.append(node)
    # 初始化所有叶子节点的层级为1
    leafs = []
    branch_res = {"Level1":{"Number":0, "Angle":0, "Length":0, "Radii":0, "Branch Counter":0}}
    for leaf in leaf_nodes:
        leafs.append(leaf.value)
        leaf.level = 1
        branch_res["Level1"]["Number"] += 1

    
    # 从叶子节点开始逐层向上更新每个节点的层级
    down_depth = list(node_depth)
    down_depth.sort(reverse=True)
    for d in down_depth:
        nodes = node_depth[d]
        for node in nodes:
            t_num = False
            if node.children:
                child_levels = [child.level for child in node.children]
                #print(child_levels)
                if len(child_levels) == 1:
                    node.level = child_levels[0]
                elif len(child_levels) == len(list(set(child_levels))):
                    node.level = max(child_levels)
                else:
                    dic = {}
                    for level in child_levels:
                        if level not in dic:
                            dic[level] = 1
                        else:
                            dic[level] += 1
                    levels = list(dic.keys())
                    levels.sort(reverse=True)
                    new_levels = []
                    for level in levels:
                        if dic[level] > 1:
                            new_levels.append(level)
                    max_new = max(new_levels)
                    max_old = max(levels)
                    #print(new_levels, levels)
                    if max_new >= max_old:
                        # [3,3,1] 
                        node.level = max_new + 1
                        t_num = True
                    else:
                        # [3,1,1]
                        node.level = max_old
                if t_num:
                    #print(branch_res)
                    branch_res = assign_number(branch_res, node.level)
    return branch_res

def assign_number(branch_res, level):
    flag = "Level" + str(level)
    if flag not in branch_res:
        branch_res[flag] = {"Number":1, "Angle":0, "Length":0, "Radii":0, "Branch Counter":0}#, "Angle":angle}
    else:
        branch_res[flag]["Number"] += 1
    return branch_res

def contruct_tree(tree, current_node, skel):
    root = TreeNode(current_node, skel.vertices[current_node])
    def build_tree(node, root, tree):
        if node in tree:
            for child in tree[node]:
                id = child[0]
                radii = child[1]
                if id == len(skel.vertices): id -= 1
                length = np.linalg.norm(skel.vertices[node] - skel.vertices[id])
                child_node = TreeNode(id, skel.vertices[id], parent=root)
                if root.parent == None:
                    root.add_child(child_node, edge_radii=radii, edge_length=length)
                else:
                    angle_radians, angle_degrees = calculate_angle_between_vectors(child_node.coords, root.coords, root.parent.coords) 
                    root.add_child(child_node, edge_radii=radii, edge_length=length, edge_angle=angle_degrees)
                build_tree(id, child_node, tree)
    build_tree(current_node, root, tree)
    return root

import math
def calculate_angle_between_vectors(A1, A2, A3):
    # 计算向量 A1A2 和 A2A3
    vector_A1A2 = (A2[0] - A1[0], A2[1] - A1[1], A2[2] - A1[2])
    vector_A2A3 = (A3[0] - A2[0], A3[1] - A2[1], A3[2] - A2[2])
    
    # 计算向量的点积
    dot_product = (vector_A1A2[0] * vector_A2A3[0] +
                   vector_A1A2[1] * vector_A2A3[1] +
                   vector_A1A2[2] * vector_A2A3[2])
    
    # 计算向量的模长
    magnitude_A1A2 = math.sqrt(vector_A1A2[0]**2 + vector_A1A2[1]**2 + vector_A1A2[2]**2)
    magnitude_A2A3 = math.sqrt(vector_A2A3[0]**2 + vector_A2A3[1]**2 + vector_A2A3[2]**2)
    
    # 如果其中一个向量的模长为零，则说明无法计算夹角
    if magnitude_A1A2 == 0 or magnitude_A2A3 == 0:
        return None, None  # 无法计算夹角
    
    # 计算夹角的余弦值
    cos_theta = dot_product / (magnitude_A1A2 * magnitude_A2A3)
    
    # 对 cos_theta 进行剪裁，确保它在 [-1, 1] 之间
    cos_theta = max(-1, min(1, cos_theta))
    
    # 计算夹角（弧度）
    angle_radians = math.acos(cos_theta)
    
    # 转换夹角为度数
    angle_degrees = math.degrees(angle_radians)
    
    return angle_radians, angle_degrees

def reverse_tree(tree, new_root):
    # 构建原始树的逆向映射
    del tree[-1]
    parent_map = {}
    for parent, children in tree.items():
        for child in children:
            #if child in parent_map:
            if child[0] in parent_map:
                #parent_map[child].append(parent)
                parent_map[child[0]].append([parent,child[1]])
            else:
                #parent_map[child] = [parent]
                parent_map[child[0]] = [[parent, child[1]]]

    # 使用新根节点构建新的树
    new_tree = {new_root: []} 
    print("tree:", tree)
    print("parent_map:",parent_map)
    print("new_tree:",new_tree)

    def add_child(tree, child_nodes, new_tree):
        for child_node in child_nodes:
            # if child_node in tree:
            #     new_tree[child_node] = tree[child_node]
            #     child_nodes = tree[child_node]
            #     new_tree = add_child(tree, child_nodes, new_tree)
            if child_node[0] in tree:
                new_tree[child_node[0]] = tree[child_node[0]]
                child_nodes = tree[child_node[0]]
                new_tree = add_child(tree, child_nodes, new_tree)     
        return new_tree
            
    def build_tree(node, new_tree, tree, pre_node=None):
        # tree : {1: [2], 2: [3, 4], 3: [5]}
        # parent_map : {2: [1], 3: [2], 4: [2], 5: [3]}
        # new_tree : {5: [3], 3: [2], 2: [1, 4]}
        # node : 5
        
        if node in parent_map:
          #print(new_tree, parent_map[node])
          for parent_node in parent_map[node]:
              parent_id = parent_node[0]
              parent_radii = parent_node[1]
              # parent_node -> child_node BECOME child_node -> parent_node
              if node in new_tree:
                  new_tree[node].append([parent_id, parent_radii])
              else:
                  new_tree[node] = [[parent_id, parent_radii]]
              
              # add original child node to new tree and child node's children are also added
              if node in tree:
                  for child_node in tree[node]:
                      if child_node[0] != pre_node:
                      #if child_node != pre_node:
                        #new_tree[node].append(child_node)
                        new_tree[node].append([child_node[0],child_node[1]])
                        new_tree = add_child(tree, [child_node], new_tree)

              # recursive
              if parent_id in tree:
                  pre_node = node
                  new_tree = build_tree(parent_id, new_tree, tree, pre_node)
        return new_tree
    
    new_tree = build_tree(new_root, new_tree,tree)
    return new_tree
# 输出节点的层数
def print_tree_levels(node, dic, lines, colors, goals, k=None, high_level = 0, branch_res={}, branch=[],
                      branch_data={}, cur_length=0, cur_radii=0, cur_counter=0, cur_angle=0):
    check_branch = [node.level == child.level for child in node.children]
    # [False, False, False, ....]
    cur_counter += 1
    if not any(check_branch) or not check_branch:
        cur_radii = cur_radii / cur_counter 
        branch.append({"Level": node.level, "ID":node.value, "Radii":cur_radii, "Length": cur_length, "Angle":cur_angle})

    for child in node.children:
        parent_point = node.value
        child_point = child.value
        length, radii, angle = node.edges[child]['length'], node.edges[child]['radii'], node.edges[child]['angle']

        #if cur_angle == 0: cur_angle = angle
        if child.level == node.level:
            branch_data[child]=[cur_length, cur_radii, cur_angle, cur_counter]
        else:
            cur_angle = angle
            branch_data[child]=[0, 0, cur_angle, 0]
        
        if length:
            branch_data[child][0] += length
            branch_res["Level"+str(child.level)]["Length"] += length
        if radii:
            branch_data[child][1] += radii
            branch_res["Level"+str(child.level)]["Radii"] += radii
        # the reason why child.level < node.level is they are the same branch
        if child.level < node.level and angle:
            branch_res["Level"+str(child.level)]["Angle"] += angle
            #dic["Level"+str(child.level)].append({"ID":child_point,"Radii":(radius/radii_counter), "Length":lengths, "Angle":angle})
            # lengths, raidus, radii_counter = 0, 0, radii_counter - 1

        
            
        points = [parent_point, child_point]
        line = tm.path.entities.Line(points=points)
        if child.level < len(colors) and (not k or (parent_point in k or child_point in k)):
            line.color = colors[child.level - 1]
        else:
            line.color = [0,0,0,255]
        if child.level == high_level:
            goals.append([node, node.edges[child]])
        lines.append(line)
        
        # if child.level not in dic:
        # dic[child.level] = [{"ID":child.value,"Radii":node.edges[child]['radii'], "Length":node.edges[child]['length'], "Angle":node.edges[child]['angle']}]
        # else:
        dic["Level"+str(child.level)].append({"ID":child.value, "Radii":node.edges[child]['radii'], "Length":node.edges[child]['length'],"Angle":node.edges[child]['angle']})
        #print(f"{node.value}->{edge['to'].value} branch_level: {edge['to'].level} radius: {edge['radii']} length: {edge['length']} angle: {edge['angle']}")
    #print("---------------------------------------------------------------------------------------------------------------------------------------")
    for child in node.children:
        cur_length, cur_radii, cur_angle, cur_counter = branch_data[child][0], branch_data[child][1], branch_data[child][2],branch_data[child][3]
        print_tree_levels(child, dic,lines, colors, goals, k=k, high_level=high_level, branch_res=branch_res, branch=branch,
                          branch_data={}, cur_length=cur_length, cur_radii=cur_radii, cur_angle=cur_angle, cur_counter=cur_counter)
    return dic, lines, goals, branch_res, branch
# # 修改 show 方法以接受骨架颜色和背景颜色参数
# # 绑定新方法到 skel 对象
def scene(self, mesh=False, **kwargs):
    """Return a Scene object containing the skeleton.

    Returns
    -------
    scene :     trimesh.scene.scene.Scene
                Contains the skeleton and optionally the mesh.

    """
    for enty in self.skeleton.entities:
        if isinstance(enty, tm.path.entities.Line):
            enty.color = [255, 0, 0, 255]
    if mesh:
        if isinstance(self.mesh, type(None)):
            raise ValueError('Skeleton has no mesh.')

        self.mesh.visual.face_colors = [100, 100, 100, 100]

        # Note the copy(): without it the transform in show() changes
        # the original meshes
        sc = tm.Scene([self.mesh.copy(), self.skeleton.copy()], **kwargs)
    else:
        sc = tm.Scene(self.skeleton.copy(), **kwargs)

    return sc

def show(self, mesh=False, **kwargs):
    """Render the skeleton in an opengl window. Requires pyglet.

    Parameters
    ----------
    mesh :      bool
                If True, will render transparent mesh on top of the
                skeleton.

    Returns
    --------
    scene :     trimesh.scene.Scene
                Scene with skeleton in it.

    """
    scene = self.scene(mesh=mesh)

    # I encountered some issues if object space is big and the easiest
    # way to work around this is to apply a transform such that the
    # coordinates have -5 to +5 bounds
    fac = 5 / np.fabs(self.skeleton.bounds).max()
    scene.apply_transform(np.diag([fac, fac, fac, 1]))

    return scene.show(**kwargs)
Skeleton.scene = scene
Skeleton.show = show

In [3]:
def new_cast_waves(mesh, step_size, origins=None, rad_agg_func=np.mean, progress=True):
    """Cast waves across mesh."""
    if not isinstance(origins, type(None)):
        if isinstance(origins, int):
            origins = [origins]
        elif not isinstance(origins, (set, list)):
            raise TypeError(
                "`origins` must be vertex ID (int) or list "
                f'thereof, got "{type(origins)}"'
            )
        origins = np.asarray(origins).astype(int)
    else:
        origins = np.array([])

    # Step size must be positive
    if step_size < 0:
        raise ValueError("`step_size` must be > 0")

    # Generate Graph (must be undirected)
    G = ig.Graph(edges=mesh.edges_unique, directed=False)
    G.es["weight"] = mesh.edges_unique_length

    # Prepare empty array to fill with centers
    centers = []
    radii = []
    data = []

    # Go over each connected component
    with tqdm(
        desc="Skeletonizing", total=len(G.vs), disable=not progress, leave=False
    ) as pbar:
        # k, cc 只需要遍历一次 因为树是连通的
        # k是遍历的次数
        # cc = [0,1,2,3,....] 顶点索引
        for k, cc in enumerate(G.connected_components()):
            # Make a subgraph for this connected component
            SG = G.subgraph(cc)
            cc = np.array(cc)
            # Select seeds according to the number of waves
            pot_seeds = np.arange(len(cc))
            np.random.seed(1985)  # make seeds predictable
            # See if we can use any origins
            if len(origins):
                # Get those origins in this cc
                in_cc = np.isin(origins, cc)
                if any(in_cc):
                    # Map origins into cc
                    cc_map = dict(zip(cc, np.arange(0, len(cc))))
                    seed = np.array([cc_map[o] for o in origins[in_cc]])[0]
                else:
                    seed = np.random.choice(pot_seeds)
            else:
                seed = np.random.choice(pot_seeds)

            # Get the distance between the seed and all other nodes
            # dist是种子点和其他点的距离
            dist = np.array(
                SG.distances(source=seed, target=None, mode="all", weights="weight")
            )[0]
            # What's the max distance we can reach?
            # mx = dist中最大值
            mx = dist[dist < float("inf")].max()
            # To keep track of which vertices we have already processed and can be
            # safely ignored
            # dist中为0的元素为True 否则为False
            # dist = [0, 1.5, 2, 0] -> is_inside_vert = [True, False, False, True]
            is_inside_vert = np.zeros(len(dist)).astype(bool)

            # Collect groups
            # i: index | d: distance
            # mx = 500, step_size = 25 -> i: 0, 1, 2, 3, 4,... | d: 0, 25, 50, 75, 100, ... 
            for i, d in enumerate(np.arange(0, mx, step_size)):
                # Inner verts are all vertices that are within the current distance
                # (minus those that we have already processed
                # 识别出哪些顶点距离在范围内 并且 没有被处理过
                # dist = [10, 20, 24, 50, 100] | d = 25 | is_inside_vert = [False, True, True, True, True]
                # -> inside_verts = [1,2,3]
                inside_verts = np.where((dist <= d) & ~is_inside_vert)[0]

                # To get the outer edge, we need to (1) find the neighbors of the inner edge
                # 找到inside_verts中各个顶点相邻的点
                # inside_verts = [p2, p3] | p2 -> p4 and p2 -> p5 | p3 -> p6 and p3 -> p7 | -> neighbors = [[p4,p5], [p6,p7]]
                neighbors = [
                    np.array(nn) for nn in SG.neighborhood(vertices=inside_verts)
                ]
                # (2) only keep those whose distance is above the current distance (i.e. those going outwards)
                # 筛选出neighbors中的哪些顶点和seed距离大于d
                # outer_verts : inside_verts's neighbours but distance > d
                # seed = p1 | d = 25 | distance(p1, p4) = 10 distance(p1, p5) = 20, ->p6=30, ->p7=40... | -> outer_verts = [p6, p7]
                outer_verts = [nn[dist[nn] > d] for nn in neighbors] # and nn[dist[nn]] < d + step_size

                # Inside vertices that are not part of the inner ring(s) have no neighbors outside
                # inside_verts = [A, B, C] | outer_verts = [[D], []. [E, F]] 
                # -> is_inside_edge = [True, False, True] | inner_verts = [A, C] | outer_verts = [[D], [E, F]]
                is_inside_edge = np.array([len(ov) > 0 for ov in outer_verts]) # 筛选出outer_verts中不为空的列表
                inner_verts = inside_verts[is_inside_edge] # inner_verts筛选出insde_verts中有与outer_vert相邻的点 -> v_inside <= d and v_outer > d
                outer_verts = [
                    ov for ov, is_iv in zip(outer_verts, is_inside_edge) if is_iv
                ] # inner_verts对应的邻居

                # To avoid doing the same work twice, we will mark inner vertices
                # inside_verts = [A, B, C] | is_inside_edge = [True, False, True]
                # -> is_inside_vert = [...,(A)True, (B)False, (C)True,...]
                is_inside_vert[inside_verts[~is_inside_edge]] = True

                # For each edge between inner-vertices and their outer neighbors calculate the
                # exact position for the exact step_size distance
                in_out_edges = np.array(
                    [
                        [iv, ov]
                        for iv, ovs in zip(inner_verts, outer_verts)
                        for ov in ovs
                    ]
                )
                in_pos = mesh.vertices[cc[in_out_edges[:, 0]]]
                out_pos = mesh.vertices[cc[in_out_edges[:, 1]]]

                # The distance between the inner and outer vertices
                in_out_dist = in_out_dist = np.sqrt(
                    ((in_pos - out_pos) ** 2).sum(axis=1)
                )

                # For each in_out_edge the remaining distance
                # d = 25 | distance(seed, inner_vert(A)) = 13 | -> d_left = 25 - 13 = 12
                d_left = d - dist[in_out_edges[:, 0]]

                # Move along the edges until we hit the target distance
                # 在inner_vert和outer_vert的边上滑动 找到innert_vert到outer_vert的edge上 distance(inner_vert, new_vert) = d_left 的 new_vert
                new_verts = (
                    in_pos + (out_pos - in_pos) * (d_left / in_out_dist)[:, None]
                )

                # To group vertices into rings we need to first determine which vertices
                # are part of the same ring. We do this by checking which outer vertices
                # are in connected components
                outer_verts_unique = np.unique(np.concatenate(outer_verts)) # 将所有outer_verts变成一个不重复数组: [[E,F], [E, G]] -> [E, F ,G]
                # SG.subgraph(outer_verts_unique) = [B, C, E, F]
                # if B - C and E - F | -> SG.subgraph(other_verts_unique).connected_components() = [[B,C], [E,F]]
                # first loop: cc2 = [0, 1] , second loop: cc2 = [2, 3] , ...
                #print("cc2 connected_components:",SG.subgraph(outer_verts_unique).connected_components())
                for cc2 in SG.subgraph(outer_verts_unique).connected_components():
                    #print("cc2", cc2)
                    # Translate this connected components back to the vertex IDs in SG
                    # cc2 = [0, 1] | outer_verts_unique = [B, C, E, F] | -> outer_verts_cc2 = [B, C]
                    outer_verts_cc2 = outer_verts_unique[cc2]

                    # Get the new vertices that are part of this connected component
                    # From new_verts, find vertices corresponding to the ring (outer vertices)
                    this_new_verts = new_verts[
                        np.isin(in_out_edges[:, 1], outer_verts_cc2)
                    ]

                    # Get the center of this connected component
                    # Get the center of ring
                    this_center = this_new_verts.mean(axis=0)

                    # Calculate the radius of this connected component
                    # Calculate the distance from each new_vertices to the center, add together and get the mean value - radius
                    this_radius = rad_agg_func(
                        np.sqrt((this_new_verts - this_center) ** 2).sum(axis=1)
                    )

                    centers.append(this_center)  # Store the center
                    radii.append(this_radius)  # Store the radius
                    data.append(
                        (k, i, cc[outer_verts_cc2[0]])
                    )  # Track the connected component, the step and a vertex from the outer ring for this center
                    # i: current_seed -> [0] step_size -> [1] 2 * step_size -> [2] 3 * ... each i could have multi centers

                # pbar.update(len(cc))
                # Update progress bar based on the number of vertices we have invalidated
                pbar.update((~is_inside_edge).sum())

    centers = np.vstack(centers)
    radii = np.array(radii)
    data = np.array(data)
    # print(data)
    # Next we have to reconstruct the parent-child relationships
    # For each center, we know _a_ vertex that is part of the (outer) ring
    # With that information we can ask, for each center, which center in the
    # previous step is closest to it (as per distance along the mesh)
    parents = np.full(len(centers), fill_value=-1, dtype=int) # initialize parent nodes with the size of centers -> parents = [-1,-1,-1,...]
    num_centers = len(centers)

    # for i in range(num_centers):
    #     # if i == 10:
    #     #     break
    #     for j in range(i + 1, num_centers):  # 避免重复检查
    #         if parents[i] == -1 and are_connected(centers[i], centers[j], radii[i], radii[j]):
    #             parents[i] = j

    # This maps the step(i) and the vertex ID(cc[outer_verts_cc2[0]]) to the index in the centers array 
    # step_id_map = { (1, 10): 0,  # 第1步顶点ID为10的中心点对应data中的第0行
    #                 (1, 11): 1,  # 第1步顶点ID为11的中心点对应data中的第1行
    #                 (2, 20): 2,  # 第2步顶点ID为20的中心点对应data中的第2行
    #                 (2, 21): 3,  # 第2步顶点ID为21的中心点对应data中的第3行
    #                 (3, 30): 4,  # 第3步顶点ID为30的中心点对应data中的第4行
    #                 (3, 31): 5}  # 第3步顶点ID为31的中心点对应data中的第5行
    step_id_map = {(step, id): i for i, (step, id) in enumerate(data[:, 1:])}
    tree = G.spanning_tree()

    for i in trange(
        1, data[:, 1].max(), desc="Connecting", disable=not progress, leave=False
    ): # data[:, 1].max() = 3, means there are 3 steps totally -> for i in trange(1, 3)
        #if i == 100: break
        is_this_step = data[:, 1] == i  # All centers in this step
        # if i = 2, is_this_step = [False, False, True, True, False, False] which means the center of second step is at data[2] and data[3]
        is_prev_step = data[:, 1] == i - 1  # All centers in the previous step
        # i - 1 = 1, is_prev_step = [True, True, False, False, False, False] which means the center of previous step is at data[0] and data[1]

        # If there is only one center in the previous step, we can just go on and connect these
        # previous centers only have one center
        if is_prev_step.sum() == 1:
            parents[is_this_step] = np.where(is_prev_step)[0][0]
            continue

        this_step_track_centers = centers[is_this_step]
        prev_step_track_centers = centers[is_prev_step]
        this_step_track_verts = np.unique(
            data[is_this_step, 2]
        )  # All track-vertices in this step
        prev_step_track_verts = np.unique(
            data[is_prev_step, 2]
        )  # All track-vertices in the previous step

        # Get distances between current and previous track vertices
        # Note to self: this step takes up about 60% of the time at the moment
        # There should be a way to speed this up.
        # vertices = [10, 11, 20, 21, 30, 31] | this_step_track_verts = [20, 21] | prev_step_track_verts = [10, 11]
        # According to the connection relationship of the tree, get the min distance from 'this_step_track_verts' to 'prev_step_track_verts' 
        # min_dist(20 -> 10), min_dist(20 -> 11), min_dist(21 -> 10), min_dist(21 -> 11), ...
        # -> d = [[3.0, 2.0],[1.5, 2.5]]
        # d 是当前步骤聚合的所有点 到 上一步骤聚合的所有点的最小距离
        d = np.linalg.norm(
        this_step_track_centers[:, np.newaxis, :] - prev_step_track_centers[np.newaxis, :, :],
        axis=2
        )
        # Get the closest previous track-vertex for each current track-vertex
        # d.argmin(axis=1) returns the index of min value of each element 
        # d = [[3.0, 2.0],[1.5, 2.5]] | min([3.0, 2.0]) = 2.0 = index(1) | min([1.5, 2.5]) = 1.5 = index(0) | d.argmin(axis=1) = [1, 0]
        # prev_step_track_verts = [10, 11] | d.argmin(axis=1) = [1, 0] | cloest_prev_track_verts = prev_step_track_verts[d.argmin(axis=1) = [11, 10]
        # 说明 node 20 到 node 11 距离最短 | node 21 到 node 10 距离最短
        # cloest_prev_track_verts 是 找到上一步骤聚合的所有点的 离 当前步骤所有点最近的 点
        closest_prev_track_verts = prev_step_track_verts[d.argmin(axis=1)]
        # 将this_step_track_verts 和 cloest_prev_track_verts中的一一对应
        # this_step_track_verts = [20, 21] | cloest_prev_track_verts = [11, 10] | i = 2 | 
        # is_this_step = [False,False,True,True,False,False] 代表的当前[21, 20]对应的是index 2 3
        for this, prev in zip(this_step_track_verts, closest_prev_track_verts):
            # parents[2] = step_id_map[(1, 11)] = 1 | parents[3] = step_id_map[(1, 10)] = 1
            parents[is_this_step & (data[:, 2] == this)] = step_id_map[(i - 1, prev)]
    return centers, radii, parents

In [4]:
import skeletor.skeletonize
import igraph as ig
import numpy as np
import pandas as pd

from tqdm.auto import tqdm, trange

from skeletor.utilities import make_trimesh
def new_by_wavefront_exact(mesh, step_size, origins=None, radius_agg="mean", progress=True):
    """Skeletonize a mesh using wave fronts.

    This is the _exact_ version of the `by_wavefront` function meaning
    that each wave front moves exactly the given distance (see `step_size`)
    along the mesh, instead of hoping from vertex to vertex. This is
    computationally more expensive but also more accurate.

    Parameters
    ----------
    mesh :          mesh obj
                    The mesh to be skeletonize. Can an object that has
                    ``.vertices`` and ``.faces`` properties  (e.g. a
                    trimesh.Trimesh) or a tuple ``(vertices, faces)`` or a
                    dictionary ``{'vertices': vertices, 'faces': faces}``.
    step_size :     float | int (>0)
                    The distance each the wave fronts move along the mesh
                    in each step.
    origins :       int | list of ints, optional
                    Vertex ID(s) where the wave(s) are initialized. If there
                    is no origin for a given connected component, will fall
                    back to semi-random origin.
    radius_agg :    "mean" | "median" | "max" | "min" | "percentile75" | "percentile25"
                    Function used to aggregate radii over sample (i.e. the
                    vertices forming a ring that we collapse to its center).
    progress :      bool
                    If True, will show progress bar.

    Returns
    -------
    skeletor.Skeleton
                    Holds results of the skeletonization and enables quick
                    visualization.

    """
    agg_map = {
        "mean": np.mean,
        "max": np.max,
        "min": np.min,
        "median": np.median,
        "percentile75": lambda x: np.percentile(x, 75),
        "percentile25": lambda x: np.percentile(x, 25),
    }
    assert radius_agg in agg_map, f'Unknown `radius_agg`: "{radius_agg}"'
    rad_agg_func = agg_map[radius_agg]

    mesh = make_trimesh(mesh, validate=False)

    centers_final, radii_final, parents = new_cast_waves(
        mesh,
        step_size=step_size,
        origins=origins,
        rad_agg_func=rad_agg_func,
        progress=progress,
    )

    # Map radii for individual vertices to the collapsed nodes
    # Using pandas is the fastest way here
    swc = pd.DataFrame()
    swc["node_id"] = np.arange(0, len(centers_final))
    swc["parent_id"] = parents
    swc["x"] = centers_final[:, 0]
    swc["y"] = centers_final[:, 1]
    swc["z"] = centers_final[:, 2]
    swc["radius"] = radii_final

    return Skeleton(swc=swc, mesh=mesh, method="wavefront_exact")
skeletor.skeletonize.by_wavefront_exact = new_by_wavefront_exact


### Skeleton

In [5]:
#m = tm.load('/Users/hcj/科研/new_project/Data/Skeleton Data/final model/simple_0.01/final_model(simple_0.01).stl')
m = tm.load('/Users/hcj/科研/new_project/PV_simple_0.01.stl')
fixed = sk.pre.fix_mesh(m, remove_disconnected=100, inplace=False)
skel = sk.skeletonize.by_wavefront_exact(fixed, origins=50,step_size=50)
skel.show(mesh=True)

Skeletonizing:   0%|          | 0/89859 [00:00<?, ?it/s]

Connecting:   0%|          | 0/243 [00:00<?, ?it/s]

In [7]:
skel.save_swc("skel_PV.swc")

In [6]:
import octarine as oc 
radius_exact = skel.radius[0].copy()
vertices_exact = skel.vertices.copy()
radius_exact = radius_exact
vertices_exact = vertices_exact
# Open a viewer 
# (if you're in an iPython terminal you may have to start a gui event loop via e.g. `%gui qt6`)
v = oc.Viewer()
v.resize((1000,1000))
v.center_camera()
# Add the skeleton points
v.add_points(vertices_exact, size=radius_exact, size_space='world')
v.title="Tree"
v.show(use_sidecar=True, toolbar=True)

RFBOutputContext()

JupyterOutput(children=(JupyterWgpuCanvas(css_height='1000px', css_width='1000px'), JupyterToolbar(children=(Tab(children=(VBox(children=(SelectMultiple(layout=Layout(height='200px', width='auto'), options=('Scatter',), value=()), Dropdown(layout=Layout(width='auto'), options=('Action', 'Remove selected', 'Hide selected', 'Unhide all'), tooltip='Perform action on selected objects', value='Action'), ColorPicker(value='white', layout=Layout(width='auto'), tooltip='Set color for selected objects'), Button(description='Center Camera', icon='align-center', layout=Layout(width='auto'), style=ButtonStyle(), tooltip='Auto-center camera'), Button(description='Screenshot', icon='camera', layout=Layout(width='auto'), style=ButtonStyle(), tooltip='Take a screenshot')), layout=Layout(width='auto')), VBox(children=(Checkbox(value=False, description='Flat shading', indent=False, layout=Layout(width='auto')), Checkbox(value=False, description='Wireframe', indent=False, layout=Layout(width='auto')), Ch

In [8]:
max1 = max(skel.radius[0])
print(list(skel.radius[0]).index(max1))

2469


In [9]:
edge_map = {}
with open('/Users/hcj/科研/new_project/skel_PV.swc', 'r') as f:
  for line in f:
    if line.startswith('#'):
      continue
    parts = line.split()
    child_node = int(parts[0])
    parent_node = int(parts[6])
    radius = float(parts[5])
    if parent_node not in edge_map:
      edge_map[parent_node] = [[child_node, radius]]
    else:
      edge_map[parent_node].append([child_node, radius])

In [10]:
# 设置新的根节点
new_root = 2469
# 生成新的树
new_tree = reverse_tree(edge_map, new_root)

tree: {0: [[1, 28.025203731692102]], 1: [[2, 43.922027287283825]], 2: [[3, 32.55538175889552], [4, 57.84107401491458]], 3: [[5, 30.78119607950825]], 4: [[6, 56.89923146645084]], 5: [[7, 14.35556316085649], [8, 13.355314256137444]], 6: [[9, 18.24194941139158], [10, 73.37196674805706]], 8: [[11, 5.136163322496524]], 10: [[12, 52.41595502625397]], 12: [[13, 48.86335298988252]], 13: [[14, 60.15097476949475], [15, 30.62916014666356]], 14: [[16, 45.594431393316086]], 15: [[17, 31.62854619492617]], 16: [[18, 44.277892373978474]], 18: [[19, 44.26974345968504]], 19: [[20, 44.24694923305944]], 20: [[21, 44.23163966419988]], 21: [[22, 46.47745366766289]], 22: [[23, 32.771337013718494], [24, 59.81674925868591]], 23: [[25, 32.11439147954147]], 24: [[26, 52.57086468875467]], 25: [[27, 42.78332667859409]], 26: [[28, 50.61250637019037]], 27: [[29, 26.525526780059636], [30, 19.702194920819466]], 28: [[31, 51.59962951222479]], 29: [[32, 37.98464117552174]], 30: [[33, 11.302376858416665]], 31: [[34, 64.4

In [15]:
import trimesh as tm
import pyglet

# Your existing tree construction logic
# colors = [
#     [255, 0, 0, 255], [0, 100, 0, 255], [0, 255, 0, 255],
#     [135, 206, 235, 255], [0, 0, 255, 255],
#     [255, 0, 255, 255], [220, 20, 60, 255], [178, 34, 34, 255]
# ]
colors = [
    [0, 0, 0, 255], [0, 0, 0, 255], [0, 0, 0, 255],
    [0, 0, 0, 255], [0, 0, 0, 255],
    [255, 0, 0, 255], [0, 0, 0, 255], [0, 0, 0, 255]
]

# Construct tree and path
tree = contruct_tree(new_tree, new_root, skel)
branch_res = assign_levels(tree)
dic = {}
for key in branch_res.keys():
    dic[key] = []

In [16]:
dic, lines, goals, branch_res, branch = print_tree_levels(tree, dic, [], colors, [], k=None, high_level=0, branch_res=branch_res)
print(branch)
for key in branch_res.keys():
    branch_res[key]["Length"] /= branch_res[key]["Number"]
    branch_res[key]["Angle"] /= branch_res[key]["Number"]
    if len(dic[key]) != 0:branch_res[key]["Radii"] /= len(dic[key])

[{'Level': 8, 'ID': 2469, 'Radii': 0.0, 'Length': 0, 'Angle': 0}, {'Level': 5, 'ID': 374, 'Radii': 144.24474723895233, 'Length': 1040.3214871954315, 'Angle': 108.7894095668669}, {'Level': 4, 'ID': 38, 'Radii': 96.82047841037475, 'Length': 2539.8726753430656, 'Angle': 117.92614772124395}, {'Level': 3, 'ID': 22, 'Radii': 56.48660147386365, 'Length': 349.9756516381465, 'Angle': 50.994612710320546}, {'Level': 1, 'ID': 0, 'Radii': 35.97361550948796, 'Length': 92.3241900213279, 'Angle': 27.191704159116885}, {'Level': 2, 'ID': 5, 'Radii': 48.71266018895424, 'Length': 736.8593770552151, 'Angle': 27.191704159116885}, {'Level': 1, 'ID': 7, 'Radii': 14.35556316085649, 'Length': 55.13869713879706, 'Angle': 19.717500569917256}, {'Level': 1, 'ID': 11, 'Radii': 9.245738789316984, 'Length': 100.02168263030765, 'Angle': 47.65766789992601}, {'Level': 1, 'ID': 9, 'Radii': 18.24194941139158, 'Length': 82.49747720975702, 'Angle': 43.85027411701019}, {'Level': 1, 'ID': 17, 'Radii': 31.128853170794862, 'Leng

In [117]:
df1 = pd.DataFrame(branch)
df1.to_excel("output.xlsx")

In [13]:
import pandas as pd
df = pd.DataFrame.from_dict(branch_res, orient='index')
print(df)

        Number      Angle       Length       Radii  Branch Counter
Level1    2569  49.757595   162.862621   24.121285               0
Level2     678  55.540050   327.396560   41.249651               0
Level3     192  60.322974   527.864231   57.825130               0
Level4      50  64.654882   882.595297   81.262618               0
Level5      14  69.368528  1092.688607  124.428794               0
Level6       5  89.755415  1684.241494  177.418224               0
Level7       2   0.000000  1603.917745  283.081996               0
Level8       1   0.000000     0.000000    0.000000               0


In [36]:
#goals[0].value
z = 0
total_r = 0
points = []
n = 1
for i in range(len(goals)):
    points.append(goals[i][0].value)
    goal = goals[i]
    r = goal[1]['radii']
    #if r > 200:
    #print(goal[0].value, r)
    total_r += r
    n += 1
    if r > 200:
        print(goal[0].value)
        print(r)

    if goal[0].coords[1] > z:
        z = goal[0].coords[1]
        xyz = goal[0].coords
        index = goal[0].value
        #print(goal.coords)
total_r /= n
print(index)
print(z)
print(xyz)
print(total_r)
print(points)

NameError: name 'index' is not defined

In [17]:
# Create Path3D object
path = tm.path.Path3D(entities=lines, vertices=skel.vertices)

# Create a scene and add the Path3D geometry
scene = tm.Scene()
scene.add_geometry(path)
scene.show()
# # Try saving the image without showing the scene
# try:
#     image = scene.save_image(resolution=[800, 600], visible=False)
#     with open('path_visualization.png', 'wb') as f:
#         f.write(image)
# except Exception as e:
#     print(f"Error during rendering or saving image: {e}")